# CSE6242 - HW3 - Q1

Pyspark Imports

In [1]:
### DO NOT MODIFY THIS CELL ###
import pyspark
from pyspark.sql import SQLContext
from pyspark.sql.functions import hour, when, col, date_format, to_timestamp, round, coalesce

Initialize PySpark Context

In [2]:
### DO NOT MODIFY THIS CELL ###
sc = pyspark.SparkContext(appName="HW3-Q1")
sqlContext = SQLContext(sc)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/10/19 06:47:52 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4042. Attempting port 4043.
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4043. Attempting port 4044.
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4044. Attempting port 4045.
23/10/19 06:47:52 WARN Utils: Service 'SparkUI' could not bind on port 4045. Attempting port 4046.
/usr/local/lib/python3.9/dist-packages/pyspark/sql/context.py:113: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOr

Define function for loading data

In [3]:
### DO NOT MODIFY THIS CELL ###
def load_data():
    df = sqlContext.read.option("header",True) \
     .csv("yellow_tripdata_2019-01_short.csv")
    return df

### Q1.a

Perform data casting to clean incoming dataset

In [4]:
def clean_data(df):
    '''
    input: df a dataframe
    output: df a dataframe with the all the original columns
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql.types import StructField, StructType, IntegerType, TimestampType, FloatType, StringType

    df = df.withColumn("passenger_count", df["passenger_count"].cast(IntegerType()))
    df = df.withColumn("total_amount", df["total_amount"].cast(FloatType()))
    df = df.withColumn("tip_amount", df["tip_amount"].cast(FloatType()))
    df = df.withColumn("trip_distance", df["trip_distance"].cast(FloatType()))
    df = df.withColumn("fare_amount", df["fare_amount"].cast(FloatType()))
    df = df.withColumn("tpep_pickup_datetime", df["tpep_pickup_datetime"].cast(TimestampType()))
    df = df.withColumn("tpep_dropoff_datetime", df["tpep_dropoff_datetime"].cast(TimestampType()))

    # END YOUR CODE HERE -----------
    
    return df

### Q1.b

Find rate per person for based on how many passengers travel between pickup and dropoff locations. 

In [5]:
def common_pair(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - PULocationID
            - DOLocationID
            - passenger_count
            - per_person_rate
            
    per_person_rate is the total_amount per person for a given pair.
    
    '''
    
    # START YOUR CODE HERE ---------

   
    
    # END YOUR CODE HERE -----------
    
    return df

### Q1.c

Find trips which trip distances generate the highest tip percentage.

In [6]:
def distance_with_most_tip(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - trip_distance
            - tip_percent
            
    trip_percent is the percent of tip out of fare_amount
    '''
    
    # START YOUR CODE HERE ---------

    # END YOUR CODE HERE -----------
    
    return df


### Q1.d

Determine the average speed at different times of day.

In [7]:
def time_with_most_traffic(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - time_of_day
            - am_avg_speed
            - pm_avg_speed
            
    trip_percent is the percent of tip out of fare_amount
    
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql.functions import date_format
    from pyspark.sql import Window
    from pyspark.sql.functions import ceil,sum
    df_q1d = df.select('*')
    
    # You will be modifying the function time_with_most_traffic to determine which hour of the day has the most traffic. 
    
    df_q1d = df_q1d.withColumn('time_of_day_str',date_format(col("tpep_pickup_datetime"),"K"))
    df_q1d = df_q1d.withColumn('12_hour_time', col('time_of_day_str').cast("int"))
    
    df_q1d = df_q1d.withColumn('AM_PM',date_format(col("tpep_pickup_datetime"),"a"))
    df_q1d = df_q1d.withColumn('trip_time_h',(col("tpep_dropoff_datetime").cast("long") - col('tpep_pickup_datetime').cast("long"))/3600)
    
    # Calculate the traffic for a particular hour using the average speed of all taxi trips which began during that hour. 
    # Calculate the average speed as the average trip_distance divided by the average trip time, as distance per hour.
    
    partition_cols = ['12_hour_time','AM_PM']
    group_by_result = df_q1d.groupBy(partition_cols).count()
    
    df_q1d  = group_by_result.join(df_q1d, partition_cols)

    df_q1d = df_q1d.withColumn("trip_distance_sum", sum("trip_distance").over(Window.partitionBy(*partition_cols)))
    df_q1d = df_q1d.withColumn("average_trip_distance",col("trip_distance_sum")/col("count"))

    df_q1d = df_q1d.withColumn("trip_time_sum", sum("trip_time_h").over(Window.partitionBy(*partition_cols)))
    df_q1d = df_q1d.withColumn("average_trip_time",col("trip_time_sum")/col("count"))

    df_q1d = df_q1d.withColumn("average_speed",col("average_trip_distance")/col("average_trip_time"))

    df_q1d = df_q1d.select(['12_hour_time','AM_PM','average_speed']).distinct()

    
    df_q1d = df_q1d.groupBy('12_hour_time').pivot('AM_PM').sum("average_speed")
    df_q1d = df_q1d.withColumnRenamed("AM","am_avg_speed").withColumnRenamed("PM","pm_avg_speed").withColumnRenamed("12_hour_time","time_of_day")
    df_q1d = df_q1d.orderBy(['time_of_day'], ascending=True)
    # df.show()
    
    # df.select(['12_hour_time','AM_PM','trip_time_h','average_trip_time','trip_distance','average_trip_distance','average_speed']).show()
    df = df_q1d
    # END YOUR CODE HERE -----------
    
    return df


### The below cells are for you to investigate your solutions and will not be graded
## Ensure they are commented out prior to submitting to Gradescope to avoid errors

In [8]:
df = load_data()
df = clean_data(df)
# common_pair(df)
# distance_with_most_tip(df)
# time_with_most_traffic(df)

# # # q1b
# q1b_df = common_pair(df)
# # q1b_df.show()
# print("First row :",q1b_df.collect()[0][0] == '239') 
# print("First row :",q1b_df.collect()[0][1] == '238') 
# print("First row :",q1b_df.collect()[0][2] == 62) 
# print("First row :",q1b_df.collect()[0][3] == 4.26274198870505) 

# print("4th row :",q1b_df.collect()[4][0] == '148') 
# print("4th row :",q1b_df.collect()[4][1] == '79') 
# print("4th row :",q1b_df.collect()[4][2] == 42) 
# print("4th row :",q1b_df.collect()[4][3] == 4.711904752822149) 

# print("9th row :",q1b_df.collect()[9][0] == '79') 
# print("9th row :",q1b_df.collect()[9][1] == '170') 
# print("9th row :",q1b_df.collect()[9][2] == 34) 
# print("9th row :",q1b_df.collect()[9][3] == 6.394705884596881) 

# # # q1c
# q1c_df = distance_with_most_tip(df)
# # q1c_df.show()
# print("First row :",q1c_df.collect()[0][0] == 1) 
# print("First row :",q1c_df.collect()[0][1] == 17.129815971513313) 

# print("Mid row :",q1c_df.collect()[6][0] == 5) 
# print("Mid row :",q1c_df.collect()[6][1] == 14.245405861990653) 

# print("Last row :",q1c_df.collect()[14][0] == 18) 
# print("Last row :",q1c_df.collect()[14][1] == 10.696822158448429) 

# # # q1d
q1d_df = time_with_most_traffic(df)
q1d_df.show()
print('checkint table:')
print("First row :",q1d_df.collect()[0][0] == 0  ,q1d_df.collect()[0][1] == 9.377696196631234,  q1d_df.collect()[0][2] == None) 
print("1 row :"    ,q1d_df.collect()[1][0] == 1  ,q1d_df.collect()[1][1] == 10.845483413697353, q1d_df.collect()[1][2] == 5.125214305177561) 
print("2 row :"    ,q1d_df.collect()[2][0] == 3  ,q1d_df.collect()[2][1] == None,               q1d_df.collect()[2][2] == 0.0) 
print("3 row :"    ,q1d_df.collect()[3][0] == 4  ,q1d_df.collect()[3][1] == None,               q1d_df.collect()[3][2] == 0.0) 
print("4 row :"    ,q1d_df.collect()[4][0] == 5  ,q1d_df.collect()[4][1] == None,               q1d_df.collect()[4][2] == 0.5137660239764732) 
print("5 row :"    ,q1d_df.collect()[5][0] == 6  ,q1d_df.collect()[5][1] == None,               q1d_df.collect()[5][2] == 9.989847870647605) 
print("6 row :"    ,q1d_df.collect()[6][0] == 7  ,q1d_df.collect()[6][1] == None,               q1d_df.collect()[6][2] == 0.18415305490417713) 
print("7 row :"    ,q1d_df.collect()[7][0] == 8  ,q1d_df.collect()[7][1] == None,               q1d_df.collect()[7][2] == 0.5183127622697896) 
print("8 row :"    ,q1d_df.collect()[8][0] == 10 ,q1d_df.collect()[8][1] == None,               q1d_df.collect()[8][2] == 0.6147483972627696) 
print("9 row :"    ,q1d_df.collect()[9][0] == 11 ,q1d_df.collect()[9][1] == None,               q1d_df.collect()[9][2] == 4.650958285207579) 


+-----------+------------------+-------------------+
|time_of_day|      am_avg_speed|       pm_avg_speed|
+-----------+------------------+-------------------+
|          0| 9.377696196631234|               NULL|
|          1|10.845483413697353|  5.125214305177561|
|          3|              NULL|                0.0|
|          4|              NULL|                0.0|
|          5|              NULL| 0.5137660239764732|
|          6|              NULL|  9.989847870647605|
|          7|              NULL|0.18415305490417713|
|          8|              NULL| 0.5183127622697896|
|         10|              NULL| 0.6147483972627696|
|         11|              NULL|  4.650958285207579|
+-----------+------------------+-------------------+

checkint table:
First row : True True True
1 row : True True True
2 row : True True True
3 row : True True True
4 row : True True True
5 row : True True True
6 row : True True True
7 row : True True True
8 row : True True True
9 row : True True True
